LET'S SEE THOSE



In [ ]:
    !pip install rarfile
!pip install wget

  Created wheel for wget: filename=wget-3.2-cp36-none-any.whl size=9682 sha256=2c71d937f16112b3cab48cf44b56eac33ae0231fe0e8bfe01cc0b035b22ea681
  Stored in directory: /root/.cache/pip/wheels/40/15/30/7d8f7cea2902b4db79e3fea550d7d7b85ecb27ef992b618f3f
Successfully built wget


DOWNLOAD AND EXTRACT!

In [ ]:
import rarfile
import os
import pathlib
from rarfile import RarFile
import wget

if os.path.exists('./data_folder.rar'):
    print('\n ** Dataset already downloaded!')
    if os.path.exists('./data_folder/135256_f05d4e4e12.jpg'):
        print('\n ** Dataset already extracted! You may proceed.')
    else:
        print('\n ** Extracting files...')
        with rarfile.RarFile("data_folder.rar", 'r') as rar:
            rar.extractall()
        print('\n ** Done! Your dataset is ready to rock!')
else:
    print('\n ** Downloading files...')
    ! wget --no-check-certificate 'https://docs.google.com/uc?export=download&id=1-R2tYoDl_P56LevfF95tP_qv1MbcVZQJ' -O dataset_images_minitest.csv
    print("\n ** Download successful. Extracting files...")
    # esse aqui tem truque por que o arquivo e pessado demais
    ! curl -c cookies "https://drive.google.com/uc?export=download&id=13zpbNNGYafdYWmdQO0-ArGjm9ipZkD5Q" > intermezzo.html
    ! curl -L -b cookies "https://drive.google.com$(cat intermezzo.html | grep -Po 'uc-download-link" [^>]* href="\K[^"]*' | sed 's/\&amp;/\&/g')" > data_folder.rar
    ! rm intermezzo.html; rm cookies

    !ls
    with rarfile.RarFile("data_folder.rar", 'r') as rar:
            rar.extractall()
    print('\n ** Done! Your dataset is ready to rock!')


 ** Downloading files...
--2020-10-27 21:43:11--  https://docs.google.com/uc?export=download&id=1-R2tYoDl_P56LevfF95tP_qv1MbcVZQJ
Resolving docs.google.com (docs.google.com)... 172.217.203.139, 172.217.203.138, 172.217.203.100, ...
Connecting to docs.google.com (docs.google.com)|172.217.203.139|:443... connected.
HTTP request sent, awaiting response... 302 Moved Temporarily
Location: https://doc-0g-5s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/9unglka3uefuf534l8lsfiluvlta65t8/1603834950000/16463329758866499058/*/1-R2tYoDl_P56LevfF95tP_qv1MbcVZQJ?e=download [following]
--2020-10-27 21:43:12--  https://doc-0g-5s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/9unglka3uefuf534l8lsfiluvlta65t8/1603834950000/16463329758866499058/*/1-R2tYoDl_P56LevfF95tP_qv1MbcVZQJ?e=download
Resolving doc-0g-5s-docs.googleusercontent.com (doc-0g-5s-docs.googleusercontent.com)... 173.194.216.132, 2607:f8b0:400c:c12::84
Connecting to doc-0g-5s-docs.goo

DATA importion!

In [ ]:
import pandas as pd
import numpy as np
import tensorflow as tf
import cv2

print("\n ** It's time to create an image tensor with those files!")
path = os.path.join('./data_folder/')

###HERE WE IMPORT THOSE LABELS WITH PANDAS
labels = pd.read_csv('dataset_images_minitest.csv',delimiter='\t', header=0)
print(labels)
###AND FOLLOWING, WE SHUFFLE THEM USING COMMAND SAMPLE RESETTING THEIR INDEX

labels=labels.iloc[np.random.permutation(labels.index)].reset_index(drop=True)
print(labels)
print(' ** How many of each can we see from labels?')

counter = 0
x_im = dict()

print(" ** It's time to check if there's already an file with x_data.")
if os.path.exists('./content/x_data.h5'):
    print(" ** Fortunately, the file is already built.")
else:
    print(" ** There isn't. It's time to build.")
    for filename in labels['filename']: 
        im= cv2.imread(path + filename)
        im = tf.image.convert_image_dtype(im, tf.float32)
        im = tf.image.rgb_to_grayscale(im)
        im = tf.image.resize(im, [101, 101])
        x_im[counter] = im
        counter = counter + 1

    print("\n ** Finally it's done!")




 ** It's time to create an image tensor with those files!
                        filename    category
0         1007270_99118848fd.jpg  graduation
1         1007274_075d925378.jpg  graduation
2      1009219698_b40b9e6d87.jpg  graduation
3        10100422_0feca68bfb.jpg  graduation
4        10100587_48faabb61a.jpg  graduation
...                          ...         ...
20982  9972086886_34cf47225c.jpg     meeting
20983  9982556644_a05ace7ac8.jpg     meeting
20984  9982564214_3c452c380a.jpg     meeting
20985  9982619334_1e577d5ca6.jpg     meeting
20986  9985209285_b57e578e41.jpg     meeting

[20987 rows x 2 columns]
                         filename    category
0       2480141091_b582fe70fd.jpg     meeting
1       9238443007_40164ccd0a.jpg  graduation
2      14071112192_899c396537.jpg     meeting
3       2356157287_770486fde5.jpg      picnic
4        482146943_b81603c8ea.jpg     meeting
...                           ...         ...
20982               p015_0057.jpg      picnic
20983  

NEXT ACTION: ACTIVATE PREPROCESSING

In [ ]:
import itertools
traintest_ratio = 0.8
crop = int(traintest_ratio*len(labels))
full = int(len(labels))
categ = labels['category']

x_data = dict(itertools.islice(x_im.items(), crop))
print(x_data)
#data = list(dict.items(x_data))
#x_data = np.array(data)
for i in x_data:
    x_data[i] = tf.convert_to_tensor(x_data[i])

x_test = dict(itertools.islice(x_im.items(), crop, full))
#test = list(dict.items(x_test))
#x_test = np.array(test)
x_test = tf.convert_to_tensor(x_test)
y_data = categ.iloc[0:crop].values
y_test = categ.iloc[crop:full].values

print(' ** Encoding classes to binary values...')
from sklearn.preprocessing import LabelEncoder
OHE = LabelEncoder()
y_data = OHE.fit_transform(y_data)
y_test = OHE.transform(y_test)

print(len(x_data), len(x_test), len(y_data), len(y_test))
print(y_data)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



ValueError: ignored

NEXT ACTION: BUILD THE MODEL!

In [ ]:
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Flatten, Conv2D, MaxPooling2D
from keras import utils
from keras.utils import to_categorical
from IPython.display import Image, display
from keras.utils import plot_model

num_classes = 3

model = Sequential()
model.add(Conv2D(32, kernel_size=(5, 5), input_shape=(101, 101, 1), 
                 activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2), strides=(2,2)))
model.add(Conv2D(64, (5, 5), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
#model.add(Dropout(0.2))
model.add(Flatten())
model.add(Dense(1000, activation='relu'))
model.add(Dense(50, activation='relu'))
model.add(Dense(num_classes, activation='softmax'))

############COMPILANDO O MODELO.
model.compile(
  optimizer='adam',
  loss='categorical_crossentropy',
  metrics=['accuracy'],
)

model.summary()

plot_model(model,  to_file="model_kaggle_challenge.png")
display(Image('model_kaggle_challenge.png'))

NOW IT'S TIME TO WORKOUT!

In [ ]:
model.fit(
  x_data,
  to_categorical(y_data), 
  epochs=10,
  batch_size=32,
)

loss, acc = model.evaluate(
  x_test,
  to_categorical(y_test)
)
print('\n ** Loss = %s; Acc = %s.' % (loss,acc))